In [1]:
!pip install -U transformers accelerate bitsandbytes

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 59.4/59.4 MB 16.1 MB/s eta 0:00:00


In [2]:
import torch
from transformers import AutoTokenizer, AutoModelForCausalLM, BitsAndBytesConfig

In [3]:
model_id = "TinyLlama/TinyLlama-1.1B-Chat-v1.0"


bnb_config = BitsAndBytesConfig(
    load_in_4bit=True,
    bnb_4bit_use_double_quant=True,
    bnb_4bit_quant_type="nf4",
    bnb_4bit_compute_dtype=torch.float16
)

In [4]:
tokenizer = AutoTokenizer.from_pretrained(model_id)
model = AutoModelForCausalLM.from_pretrained(
    model_id,
    quantization_config=bnb_config,
    device_map="auto"
)

/usr/local/lib/python3.12/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json: 0.00B [00:00, ?B/s]

tokenizer.model:   0%|          | 0.00/500k [00:00<?, ?B/s]

tokenizer.json: 0.00B [00:00, ?B/s]

special_tokens_map.json:   0%|          | 0.00/551 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/608 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/2.20G [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/124 [00:00<?, ?B/s]

In [5]:
def ask_question(question, max_new_tokens=128):
    prompt = f"<|system|>\nYou are a helpful assistant.<|user|>\n{question}<|assistant|>\n"
    inputs = tokenizer(prompt, return_tensors="pt").to(model.device)
    outputs = model.generate(
        **inputs,
        max_new_tokens=max_new_tokens,
        do_sample=True,
        top_p=0.9,
        temperature=0.7,
        repetition_penalty=1.1,
        pad_token_id=tokenizer.eos_token_id
    )
    response = tokenizer.decode(outputs[0], skip_special_tokens=True)
    if "<|assistant|>" in response:
        response = response.split("<|assistant|>")[-1].strip()
    return response

In [7]:
questions = [
    "Why is quantization useful in large language models?",
    "What are the advantages of using 4-bit quantization in large language models?",
]

for q in questions:
    print("\nQuestion:", q)
    print("Answer:", ask_question(q))


Question: Why is quantization useful in large language models?
Answer: Quantization is useful for large language models because it helps the model to represent text data as an array of numbers. This allows the model to learn patterns and relationships between words, rather than just random noise. In large language models, the number of unique words can be quite high, which makes it challenging for traditional methods like bag-of-words or frequency-based algorithms to capture all the relevant information. Quantization allows these models to capture more meaningful features of the text data, leading to improved performance on downstream tasks such as sentiment analysis, machine translation, and question answering.

Question: What are the advantages of using 4-bit quantization in large language models?
Answer: Yes, sure! Here are some of the advantages of using 4-bit quantization in large language models:
1. Better training efficiency: 4-bit quantization provides better training efficien